**SETTING UP A PYSPARK ENVIRONMENT**

In [1]:
# Download Java Virtual Machine (JVM)
!apt-get install openjdk-8-jdk-headless -qq > /dev/null

In [3]:
# Download Spark
#!wget -q https://dlcdn.apache.org/spark/spark-3.2.1/spark-3.2.1-bin-hadoop3.2.tgz
!wget -q https://archive.apache.org/dist/spark/spark-3.0.1/spark-3.0.1-bin-hadoop3.2.tgz
# Unzip the file
!tar xf spark-3.0.1-bin-hadoop3.2.tgz

In [4]:
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = '/content/spark-3.0.1-bin-hadoop3.2'

In [5]:
# Install library for finding Spark
!pip install -q findspark
# Import the libary
import findspark
# Initiate findspark
findspark.init()
# Check the location for Spark
findspark.find()


'/content/spark-3.0.1-bin-hadoop3.2'

**UPLOADING DATA FILE FOR THE IIT/NIT OPENING AND CLOSING RANK ANALYSIS**

In [6]:
from google.colab import files

In [8]:
files.upload()

Saving data.csv to data.csv


{'data.csv': b'id,year,institute_type,round_no,quota,pool,institute_short,program_name,program_duration,degree_short,category,opening_rank,closing_rank,is_preparatory\n1,2016,IIT,6,AI,Gender-Neutral,IIT-Bombay,Aerospace Engineering,4 Years,B.Tech,GEN,838,1841,0\n2,2016,IIT,6,AI,Gender-Neutral,IIT-Bombay,Aerospace Engineering,4 Years,B.Tech,OBC-NCL,408,1098,0\n3,2016,IIT,6,AI,Gender-Neutral,IIT-Bombay,Aerospace Engineering,4 Years,B.Tech,SC,297,468,0\n4,2016,IIT,6,AI,Gender-Neutral,IIT-Bombay,Aerospace Engineering,4 Years,B.Tech,ST,79,145,0\n5,2016,IIT,6,AI,Gender-Neutral,IIT-Bombay,Aerospace Engineering,4 Years,B.Tech,GEN-PWD,94,94,0\n6,2016,IIT,6,AI,Gender-Neutral,IIT-Bombay,Aerospace Engineering,4 Years,B.Tech,OBC-NCL-PWD,45,45,0\n7,2016,IIT,6,AI,Gender-Neutral,IIT-Bombay,Chemical Engineering,4 Years,B.Tech,GEN,422,1479,0\n8,2016,IIT,6,AI,Gender-Neutral,IIT-Bombay,Chemical Engineering,4 Years,B.Tech,OBC-NCL,447,974,0\n9,2016,IIT,6,AI,Gender-Neutral,IIT-Bombay,Chemical Engineering,4 Y

**INITIATING PYSPARK SESSION**

In [9]:
# Import SparkSession
from pyspark.sql import SparkSession
# Create a Spark Session
spark = SparkSession.builder.master("local[*]").getOrCreate()
# Check Spark Session Information
spark

**READING DATA**

In [10]:
df = spark.read.format("csv").option("header","true").option("inferSchema","true").option("mode","failfast").load("data.csv")

In [11]:
df.count()

64958

In [12]:
df.createOrReplaceTempView("iit")

**DATA DICT/DESCRIPTION**

In [13]:
spark.sql("select * from iit").show()
#About Data
"""In this dataset, the year-wise distribution of cutoffs for various IITs and NITs are collected and organized on the basis of stream, category, quota etc."""
# Data Dictionary
"""Variable	        Definition	                                                          Key
year	            The year of the conducted JEE exam	
institute_type	  Type of Institute (IIT or NIT)	
round_no	        The counseling round number	
quota	            The reservation quota	                                                AI: All-India, HS: Home-State, OS: Other-State, AP: Andhra Pradesh, GO: Goa, JK: Jammu & Kashmir, LA: Ladakh
pool	            The gender quota	
institute_short	  THe short name of the Institution	
program_name	    The name of the program/stream	
program_duration	The duration of the course (in years)	
degree_short	    The name of the degree (Abbreviated)	
category	        The caste category	                                                  GEN: General, OBC-NCL: Other Backward Classes-Non Creamy Layer, SC: Scheduled Castes, ST: Scheduled Tribes, GEN-PWD: General & Persons with Disabilities, OBC-NCL-PWD: Other Backward Classes & Persons with Disabilities, SC-PWD: Scheduled Castes & Persons with Disabilities, ST-PWD: Scheduled Tribes & Persons with Disabilities, GEN-EWS: General & Economically Weaker Section, GEN-EWS-PWD: General & Economically Weaker Section & Persons with Disability
opening_rank	    The opening (starting) rank for getting admission in the institution	
closing_rank	    The closing (ending) rank for getting admission in the institution	
is_preparatory	  If admission to a preparatory course is available	                    0: No, 1: Yes"""

+---+----+--------------+--------+-----+--------------+---------------+--------------------+----------------+------------+-----------+------------+------------+--------------+
| id|year|institute_type|round_no|quota|          pool|institute_short|        program_name|program_duration|degree_short|   category|opening_rank|closing_rank|is_preparatory|
+---+----+--------------+--------+-----+--------------+---------------+--------------------+----------------+------------+-----------+------------+------------+--------------+
|  1|2016|           IIT|       6|   AI|Gender-Neutral|     IIT-Bombay|Aerospace Enginee...|         4 Years|      B.Tech|        GEN|         838|        1841|             0|
|  2|2016|           IIT|       6|   AI|Gender-Neutral|     IIT-Bombay|Aerospace Enginee...|         4 Years|      B.Tech|    OBC-NCL|         408|        1098|             0|
|  3|2016|           IIT|       6|   AI|Gender-Neutral|     IIT-Bombay|Aerospace Enginee...|         4 Years|      B.Tec

**DATA ANALYSIS USING PYSPARK SQL FUNCTION**

**1. average opening ranks as per the institution type**

In [14]:
spark.sql("select avg(opening_rank),institute_type from iit group by institute_type").show()

+------------------+--------------+
| avg(opening_rank)|institute_type|
+------------------+--------------+
|14235.075031978286|           NIT|
|2438.9288557969912|           IIT|
+------------------+--------------+



**2. Avg round numbers that are gone as per the program name sort them by avg round no.**

In [15]:
spark.sql("select avg(round_no) as avg_round,program_name from iit group by program_name order by avg_round").show()                                  

+------------------+--------------------+
|         avg_round|        program_name|
+------------------+--------------------+
|               1.0|Biotechnology and...|
|               1.0|Computational Mat...|
|               1.0|Mathematics and D...|
|               1.0|Computational Eng...|
|1.2857142857142858|Artificial Intell...|
|1.3636363636363635|Data Science and ...|
|               1.5|  Energy Engineering|
|               1.5|   Chemical Sciences|
|               1.5|Statistics and Da...|
| 1.538860103626943|Artificial Intell...|
|1.5737704918032787|Mathematics & Com...|
|1.5789473684210527|Biosciences and B...|
|1.5813953488372092|Materials Enginee...|
| 1.588235294117647|Civil and Infrast...|
|1.7142857142857142|Mineral and Metal...|
|1.7894736842105263|Biomedical Engine...|
|1.8193548387096774|Engineering and C...|
|2.2037037037037037|       Biotechnology|
|2.2071428571428573|Metallurgical Eng...|
|2.2790697674418605|        Life Science|
+------------------+--------------

**3. The count of unique categories as per the program name for the institute of IIT-Bombay.**

In [20]:
spark.sql("select count(distinct category),program_name from iit where institute_short ='IIT-Bombay' group by program_name ").show()

+------------------------+--------------------+
|count(DISTINCT category)|        program_name|
+------------------------+--------------------+
|                       6|Electrical Engine...|
|                       5|   BS in Mathematics|
|                       8|Aerospace Enginee...|
|                       7|           Chemistry|
|                      10|Computer Science ...|
|                       5|Engineering Physi...|
|                       9|Electrical Engine...|
|                       5|Mechanical Engine...|
|                       9|Chemical Engineering|
|                       7|Electrical Engine...|
|                       6|Metallurgical Eng...|
|                       4|Metallurgical Eng...|
|                       7|Metallurgical Eng...|
|                       5|Environmental Sci...|
|                      10|Mechanical Engine...|
|                       7|Mechanical Engine...|
|                      10|   Civil Engineering|
|                       7|           Eco

**4. the average opening and closing rank for the institute IIT-Bombay for year 2016**

In [22]:
spark.sql("select avg(opening_rank),avg(closing_rank) from iit where institute_short ='IIT-Bombay' and year = 2016").show()

+-----------------+-----------------+
|avg(opening_rank)|avg(closing_rank)|
+-----------------+-----------------+
|            434.0|707.1309523809524|
+-----------------+-----------------+



**5. listing year,institute_type,average opening_rank and closing_rank as per year and institute and sort them by year.**

In [25]:
spark.sql("select year,institute_type,avg(opening_rank),avg(closing_rank) from iit group by 1,2 order by year").show()

+----+--------------+------------------+------------------+
|year|institute_type| avg(opening_rank)| avg(closing_rank)|
+----+--------------+------------------+------------------+
|2016|           IIT|1293.2426666666668|1763.6053333333334|
|2016|           NIT| 4322.185430463576| 7000.342163355408|
|2017|           IIT|1353.4622406639005| 1778.414937759336|
|2018|           IIT|2409.6384976525824| 2881.660928534168|
|2019|           NIT|15004.666835443039| 20455.83493670886|
|2019|           IIT|2461.7560763888887|       2939.734375|
|2020|           IIT|  2733.14280331575| 3231.173323285607|
|2020|           NIT|16672.443037974685| 22306.08405063291|
|2021|           NIT|13890.055949367088|18065.599746835444|
|2021|           IIT| 2515.705063291139|2959.4187341772154|
+----+--------------+------------------+------------------+



**6. giving the average closing rank as per the program name sort them by program name.**

In [26]:
df.groupBy("program_name").avg("closing_rank").orderBy("program_name").show()

+--------------------+------------------+
|        program_name| avg(closing_rank)|
+--------------------+------------------+
|Aerospace Enginee...|2025.0584677419354|
|Agricultural and ...|4073.8766233766232|
|Agricultural and ...| 4805.632653061224|
|Agricultural and ...| 6164.857142857143|
|     Applied Geology| 5676.978813559322|
|  Applied Geophysics| 6142.542168674699|
| Applied Mathematics|1951.8823529411766|
|        Architecture|2334.0938198064036|
|Artificial Intell...| 1388.103626943005|
|Artificial Intell...|           1999.35|
|   BS in Mathematics| 1888.504347826087|
|     Bio Engineering|           6067.94|
|Bio Medical Engin...| 20481.54676258993|
|      Bio Technology|15971.994005994005|
|Biochemical Engin...|         2725.3125|
|Biochemical Engin...| 5978.971014492754|
|Biochemical Engin...|          5371.875|
|Bioengineering wi...| 5786.051282051282|
|Biological Engine...| 3670.965277777778|
| Biological Sciences| 4965.503448275862|
+--------------------+------------

**7. listing the unique category for the is_preparatory was enabled.**

In [27]:
spark.sql("select distinct category from iit where is_preparatory = 1").show()

+-----------+
|   category|
+-----------+
|         SC|
|     SC-PWD|
|     ST-PWD|
|    GEN-PWD|
|GEN-EWS-PWD|
|OBC-NCL-PWD|
|         ST|
+-----------+



**8. listing the unique program name where is_preparatory was enabled.**

In [37]:
spark.sql("select distinct program_name from iit where is_preparatory = 1 ").show()

+--------------------+
|        program_name|
+--------------------+
|  Textile Technology|
|Civil Engineering...|
|      Bio Technology|
|Mathematics and C...|
|Industrial Chemistry|
|Civil and Infrast...|
|Petroleum Enginee...|
|Biotechnology and...|
|Data Science and ...|
|Electrical Engine...|
|Mining Machinery ...|
| Mineral Engineering|
|     Bio Engineering|
|Electronics and E...|
|Chemical Science ...|
|  Mining Engineering|
|Mechanical Engine...|
|Civil Engineering...|
|Instrumentation E...|
|Biomedical Engine...|
+--------------------+
only showing top 20 rows



**using window function answering certain questions**

In [38]:
import pyspark.sql.functions as F
from pyspark.sql import Window
import pyspark.sql.types as T

**partitioning the data as per the institute**

In [49]:
windowSpec = Window.partitionBy("institute_type")

**analysing the data by adding two more fields of average opening and closing rank as per the institute type**

In [50]:
data = df.withColumn("avg_opening_rank",F.avg(F.col("opening_rank")).over(windowSpec)).withColumn("avg_closing_rank",F.avg(F.col("closing_rank")).over(windowSpec))

In [51]:
data.show()

+-----+----+--------------+--------+-----+--------------+-------------------+--------------------+----------------+------------+-----------+------------+------------+--------------+------------------+-----------------+
|   id|year|institute_type|round_no|quota|          pool|    institute_short|        program_name|program_duration|degree_short|   category|opening_rank|closing_rank|is_preparatory|  avg_opening_rank| avg_closing_rank|
+-----+----+--------------+--------+-----+--------------+-------------------+--------------------+----------------+------------+-----------+------------+------------+--------------+------------------+-----------------+
|17424|2016|           NIT|       6|   HS|Gender-Neutral|       NIT-Warangal|      Bio Technology|         4 Years|      B.Tech|        GEN|       14338|       23013|             0|14235.075031978286|18726.34227685396|
|17338|2016|           NIT|       6|   HS|Gender-Neutral|NIT-Tiruchirappalli|Instrumentation a...|         4 Years|      B.T

**showing the cummulative result for the avg openign and closing rank as per the institute type**

In [46]:
data1 = df.groupBy("institute_type").agg(
    F.expr("avg(opening_rank)").alias("avg_opening_rank"),
    F.expr("avg(closing_rank)").alias("avg_closing_rank")
)

In [48]:
data1.show()

+--------------+------------------+-----------------+
|institute_type|  avg_opening_rank| avg_closing_rank|
+--------------+------------------+-----------------+
|           NIT|14235.075031978286|18726.34227685396|
|           IIT|2438.9288557969912| 2891.29603403738|
+--------------+------------------+-----------------+

